In [1]:
import pandas as pd
import geopandas as gpd
import momepy as mm
import numpy as np
import pyproj
import matplotlib.pyplot as plt
import osmnx
import libpysal
import utm
from shapely.geometry import box
from shapely import geometry
from time import time
from pyproj import CRS
from shapely.geometry import Polygon, Point
import seaborn as sns
from cityseer.tools import graphs, plot, io
from scipy.stats import entropy
from tqdm import tqdm
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score, classification_report

In [2]:
df = pd.read_csv("worldcities.csv")
df = df[(df['population'] > 30000) | pd.isna(df['population'])] #keep only rows where the column population is higher than 80000 or an NA value
geometry = [Point(xy) for xy in zip(df['lng'], df['lat'])]
gdf = gpd.GeoDataFrame(df, geometry=geometry, crs="EPSG:4326")

world_continents = gpd.read_file("World_Continents.geojson", crs="EPSG:4326")
cities = gpd.sjoin(gdf, world_continents, how="left", op="within")
cities['CONTINENT'] = cities['CONTINENT'].replace('Australia', 'Oceania')
cities['CONTINENT'] = cities['CONTINENT'].replace('Antarctica', 'South America')

# Keep only the first 300 largest cities on each continent
num_cit_per_cont=1000
cities = pd.concat([cities[cities['CONTINENT'] == 'Asia'].head(num_cit_per_cont), cities[cities['CONTINENT'] != 'Asia']])
cities = pd.concat([cities[cities['CONTINENT'] == 'Europe'].head(num_cit_per_cont), cities[cities['CONTINENT'] != 'Europe']])
cities = pd.concat([cities[cities['CONTINENT'] == 'North America'].head(num_cit_per_cont), cities[cities['CONTINENT'] != 'North America']])
cities = pd.concat([cities[cities['CONTINENT'] == 'Africa'].head(num_cit_per_cont), cities[cities['CONTINENT'] != 'Africa']])
cities = pd.concat([cities[cities['CONTINENT'] == 'South America'].head(num_cit_per_cont), cities[cities['CONTINENT'] != 'South America']])
cities.reset_index(inplace=True)
cities = cities.drop(columns=['index','index_right','FID','SQMI','SQKM','Shape__Area','Shape__Length'])

cities_per_continent = cities['CONTINENT'].value_counts()

print("Number of cities per continent:")
print(cities_per_continent)

grouped_df = cities.groupby('CONTINENT')
continent_datasets = {}
for continent, group in grouped_df:
    continent_datasets[continent] = group

asia_cities = continent_datasets['Asia']
europe_cities = continent_datasets['Europe']
africa_cities = continent_datasets['Africa']
namerica_cities = continent_datasets['North America']
samerica_cities = continent_datasets['South America']
oceania_cities = continent_datasets['Oceania']

/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/IPython/core/interactiveshell.py:3466: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if await self.run_code(code, result, async_=asy):


Number of cities per continent:
CONTINENT
South America    1000
Africa           1000
North America    1000
Europe           1000
Asia             1000
Oceania            90
Name: count, dtype: int64


In [3]:
def add_mm(dataset, dist):
    dataset.reset_index(inplace=True)

    for index, row in dataset.iterrows():
        try:
            city_coordinates = tuple([row['lat'], row['lng']])
            city_name = row['city']
            print(f"Doing {city_name}: {index+1}/{len(dataset)}")
    
            try:
                buildings = osmnx.features.features_from_point(city_coordinates, dist=dist, tags={'building':True})
                buildings = osmnx.projection.project_gdf(buildings)
                buildings = buildings[buildings.geom_type.isin(['Polygon', 'MultiPolygon'])]
                buildings = buildings.reset_index(drop=True).explode(index_parts=True).reset_index(drop=True)
                buildings = buildings[["geometry"]]
                
                streets_graph = osmnx.graph_from_point(city_coordinates, dist=dist+200, network_type='drive')
                streets_graph = osmnx.get_undirected(streets_graph)
                streets_graph = osmnx.projection.project_graph(streets_graph)
                streets = osmnx.graph_to_gdfs(streets_graph, nodes=False, edges=True, node_geometry=False, fill_edge_geometry=True)
                streets = streets[["geometry"]]
                
                assert buildings.crs.equals(streets.crs)
                
                buildings['uID'] = range(len(buildings))
                tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
                tessellation['cell_area'] = tessellation.area
                
                car_md = mm.AreaRatio(tessellation, buildings, "cell_area", buildings.area, "uID").series.median()
                car_std = mm.AreaRatio(tessellation, buildings, "cell_area", buildings.area, "uID").series.std()
            
                streetlen_md = streets.length.median()
                streetlen_std = streets.length.std()
                
                streetlin_md = mm.Linearity(streets).series.median()
                streetlin_std = mm.Linearity(streets).series.std()
                
            except Exception as e:
                print(f"Insufficient response for {city_name}. Skipping...")
                car_md = None
                car_std = None
                streetlen_md = None
                streetlen_std = None
                streetlin_md = None
                streetlin_std = None
    
            try:
                profile = mm.StreetProfile(streets, buildings, distance=3)
                street_width_md = profile.w.median()
                street_width_std = profile.w.std()
                
                street_width_deviation_md = profile.wd.median()
                street_width_deviation_std = profile.wd.std()
                
                street_openness_md = profile.o.median()
                street_openness_std = profile.o.std()
                
                buildings_wall_md = mm.PerimeterWall(buildings, verbose=False).series.median()
                buildings_wall_std = mm.PerimeterWall(buildings, verbose=False).series.std()
    
                W1 = libpysal.weights.Queen.from_dataframe(tessellation, ids="uID", use_index=False)
                W3 = mm.sw_high(k=3, weights=W1)
                
                buildings_adjacency_md = mm.BuildingAdjacency(buildings, W3, "uID", verbose=False).series.median()
                buildings_adjacency_std = mm.BuildingAdjacency(buildings, W3, "uID", verbose=False).series.std()
                
                buildings_neighbour_distance_md = mm.NeighborDistance(buildings, W1, 'uID', verbose=False).series.median()
                buildings_neighbour_distance_std = mm.NeighborDistance(buildings, W1, 'uID', verbose=False).series.std()
    
            except ValueError as e:
                print(f"Error: {e}")
                profile = None
                street_width_md = None
                street_width_std = None
                street_width_deviation_md = None
                street_width_deviation_std = None
                street_openness_md = None
                street_openness_std = None
                buildings_wall_md = None
                buildings_wall_std = None
                buildings_adjacency_md = None
                buildings_adjacency_std = None
                buildings_neighbour_distance_md = None
                buildings_neighbour_distance_std = None
    
            dataset.loc[index, "tessellation_car_md"] = car_md
            dataset.loc[index, "tessellation_car_std"] = car_std            
            dataset.loc[index, "streetlen_md"] = streetlen_md
            dataset.loc[index, "streetlen_std"] = streetlen_std
            dataset.loc[index, "streetlin_md"] = streetlin_md
            dataset.loc[index, "streetlin_std"] = streetlin_std
            dataset.loc[index, "street_width_md"] = street_width_md
            dataset.loc[index, "street_width_std"] = street_width_std
            dataset.loc[index, "street_width_deviation_md"] = street_width_deviation_md
            dataset.loc[index, "street_width_deviation_std"] = street_width_deviation_std
            dataset.loc[index, "street_openness_md"] = street_openness_md
            dataset.loc[index, "street_openness_std"] = street_openness_std
            dataset.loc[index, "buildings_wall_md"]=buildings_wall_md
            dataset.loc[index, "buildings_wall_std"]=buildings_wall_std
            dataset.loc[index, "buildings_adjacency_md"] = buildings_adjacency_md
            dataset.loc[index, "buildings_adjacency_std"] = buildings_adjacency_std
            dataset.loc[index, "buildings_neighbour_distance_md"] = buildings_neighbour_distance_md
            dataset.loc[index, "buildings_neighbour_distance_std"] = buildings_neighbour_distance_std
            
        except Exception as ex:
            print(f"An error occurred in iteration {index}: {ex}")
    #osmnx.utils.config(cache_folder=None)
    return dataset

In [23]:
oceania_cities = add_mm(oceania_cities, dist=800)
oceania_cities.to_csv('oceania_d800.csv', index=False)

Doing Sydney: 1/90


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [810, 125, 459, 461, 462, 413, 411, 410, 507, 444, 443, 239, 464, 235, 412, 234, 233, 59, 468, 47, 42, 25, 278, 65, 618, 78, 530, 279, 261, 555, 266, 106, 161, 551, 552, 550, 548, 117, 549, 542, 420, 162, 349, 495, 496, 940, 1069, 964, 910, 392, 976, 975, 978, 294, 291, 293, 296, 295, 23, 292].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/s

Doing Melbourne: 2/90


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [934, 465, 776, 1514, 876, 414, 675, 158, 554, 159, 64, 1576, 15, 1370, 164, 1120, 106, 933, 364, 180].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning

Doing Brisbane: 3/90


...

/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [54, 55].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Shepparton: 89/90


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [255].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Kalgoorlie: 90/90


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


In [24]:
asia_cities = add_mm(asia_cities, dist=800)
asia_cities.to_csv('asia_d800.csv', index=False)

Doing Tokyo: 1/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation does not fully match buildings. 7 element(s) collapsed during generation - unique_id: {2753, 2754, 4656, 3345, 2747, 2748, 2749}.
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [3225, 3223, 2604, 4674, 24, 52, 4678, 4676, 4680, 1965].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_wei

Doing Jakarta: 2/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [137, 832, 831, 263, 830, 838, 651].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=Tru

Doing Delhi: 3/1000


...

/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Kahramanmaraş: 999/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Fujisawa: 1000/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation does not fully match buildings. 1 element(s) collapsed during generation - unique_id: {4934}.
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


In [25]:
europe_cities = add_mm(europe_cities, dist=800)
europe_cities.to_csv('europe_d800.csv', index=False)

Doing Moscow: 1/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation does not fully match buildings. 1 element(s) collapsed during generation - unique_id: {789}.
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [629, 674].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/mini

Doing London: 2/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation does not fully match buildings. 1 element(s) collapsed during generation - unique_id: {1104}.
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [510, 2352, 2170, 2169, 999, 25, 1931, 332, 1856, 1858, 1855, 165, 708, 176, 276, 1971, 506, 699, 702, 1511, 438, 886, 212, 1507, 1012, 1011, 1484, 71, 1561, 73, 989, 987, 1520, 631, 1522, 1461, 1523, 922, 1878, 1432, 1431, 1412, 1014, 1442, 1437, 1456, 1593, 728, 925, 1413, 521, 2306, 1213, 727, 2102, 1823, 1222, 1795, 1789, 1787, 1792, 369, 585, 1990, 625, 1989, 2340, 1988, 1319, 624, 1986, 1355, 324, 1533, 740, 1977, 1975, 816, 447, 451, 452, 454, 456, 811, 2231, 858

Doing Paris: 3/1000


...

/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [48, 109].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Wrecsam: 999/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation does not fully match buildings. 2 element(s) collapsed during generation - unique_id: {1574, 1549}.
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_11441/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [1491, 1034, 1490, 1335, 7, 1903, 63, 1901, 1332, 1336, 1330, 5, 1485, 1480, 1426, 1456, 1427, 1627, 1626, 1628, 1884, 1394, 1392, 1396, 1620, 1625, 1619, 1622, 1631, 1623, 1880, 1873, 1879, 1900, 1883, 1892, 1891, 1895, 1897, 1397, 1398, 1387, 1414, 1388, 1413, 1400, 1412, 930, 651, 932, 927, 914, 1283, 929, 602, 1297, 1288, 1326, 1327, 1316, 1321, 1320, 1303, 1304, 2157, 1459, 601, 1328, 1322, 2158, 1308, 1738, 502, 1737, 1315, 1312, 1493, 1516, 1486, 1484, 1449

Doing Pervomaisk: 1000/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


In [4]:
africa_cities = add_mm(africa_cities, dist=800)
africa_cities.to_csv('africa_d800.csv', index=False)

Doing Cairo: 1/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_31286/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [507, 673, 220].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Kinshasa: 2/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Luanda: 3/1000


...

/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Nzega: 999/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Rumonge: 1000/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


In [5]:
namerica_cities = add_mm(namerica_cities, dist=800)
namerica_cities.to_csv('namerica_d800.csv', index=False)

Doing Mexico City: 1/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_31286/201842583.py:26: UserWarning: Tessellation does not fully match buildings. 1 element(s) collapsed during generation - unique_id: {1495}.
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_31286/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [65, 1222, 2557, 2556, 454, 2582, 1038, 1985, 2015, 2662, 2661, 37, 1524, 1310].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.

Doing New York: 2/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Los Angeles: 3/1000


...

/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Acatzingo: 999/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Coconut Creek: 1000/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


In [6]:
samerica_cities = add_mm(samerica_cities, dist=800)
samerica_cities.to_csv('samerica_d800.csv', index=False)

Doing São Paulo: 1/1000


/var/folders/v5/mcnrdbxj26l_3pq9rm9nds580000gn/T/ipykernel_31286/201842583.py:26: UserWarning: Tessellation contains MultiPolygon elements. Initial objects should  be edited. `unique_id` of affected elements: [3675, 3829, 3835, 3833, 3831, 1718, 1589, 1598, 3834, 2427, 34, 3506, 2560, 107, 3723, 5, 2558, 3800, 3059, 2563, 2643, 2559, 3065, 2540, 13, 3818, 3686, 3693, 3625, 201, 496, 202, 206, 18, 531].
  tessellation = mm.Tessellation(buildings, "uID", limit=box(*buildings.total_bounds), verbose=False).tessellation
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default

Doing Buenos Aires: 2/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Rio de Janeiro: 3/1000


...

/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Coroatá: 999/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


Doing Cajazeiras: 1000/1000


/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)
/Users/janmagnuszewski/miniconda3/envs/geo/lib/python3.11/site-packages/momepy/dimension.py:890: FutureWarning: `use_index` defaults to False but will default to True in future. Set True/False directly to control this behavior and silence this warning
  spatial_weights = Queen.from_dataframe(gdf, silence_warnings=True)


In [ ]:
asia_cities
plt.figure(figsize=(8, 6))
sns.heatmap(asia_cities.isnull(), cmap='viridis', cbar=False, yticklabels=False)
plt.title('Missing Values in DataFrame')
plt.show()